In [1]:
import torch
from models import model_dict
import os

from dataset import IrisDataset
from dataset import transform
from torch.utils.data import DataLoader 

import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
from utils import get_predictions

In [2]:
# arguments
useGPU = "cuda" # or cpu
modelname = 'densenet'
filename='./best_model.pkl'
bs = 1 # batch size
save = 'test11' # path

In [3]:
os.environ["CUDA_VISIBLE_DEVICES"] = "0"
# setup model with GPU
model = model_dict[modelname]
device= torch.device(useGPU)
# Load the model from the .pkl file
model.load_state_dict(torch.load(filename))
model = model.to(device)
# evaluate model
model.eval()

/home/eecs/lucymeng/.local/lib/python3.10/site-packages/torch/cuda/__init__.py:611: UserWarning: Can't initialize NVML
  warnings.warn("Can't initialize NVML")


DenseNet2D(
  (down_block1): DenseNet2D_down_block(
    (conv1): Conv2d(1, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (conv21): Conv2d(33, 32, kernel_size=(1, 1), stride=(1, 1))
    (conv22): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (conv31): Conv2d(65, 32, kernel_size=(1, 1), stride=(1, 1))
    (conv32): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (max_pool): AvgPool2d(kernel_size=None, stride=None, padding=0)
    (relu): LeakyReLU(negative_slope=0.01)
    (dropout1): Dropout(p=0.2, inplace=False)
    (dropout2): Dropout(p=0.2, inplace=False)
    (dropout3): Dropout(p=0.2, inplace=False)
    (bn): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  )
  (down_block2): DenseNet2D_down_block(
    (conv1): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (conv21): Conv2d(64, 32, kernel_size=(1, 1), stride=(1, 1))
    (conv22): Conv2d(32, 32, kernel_size=(3, 3), stride=

In [4]:
print(type(model))

INPUT_XDIM = 400
INPUT_YDIM = 640

# bs , number of channels, xdim,
x = torch.randn(bs, 1, INPUT_XDIM, INPUT_YDIM, requires_grad=False).to(device)
model_outputfile = "best_model_bs1.onnx"
torch.onnx.export(model,               # model being run
                x,                         # model input (or a tuple for multiple inputs)
                model_outputfile,   # where to save the model (can be a file or file-like object)
                export_params=True,        # store the trained parameter weights inside the model file
                opset_version=12,          # the ONNX version to export the model to
                # do_constant_folding=True,  # whether to execute constant folding for optimization
                do_constant_folding=False,  # whether to execute constant folding for optimization
                input_names = ['input'],   # the model's input names
                output_names = ['output'], # the model's output name
)

# ===================== from rose =====================
# reference: https://github.com/ucb-bar/RoSE/blob/a743406eed87abe10dced40f141e9739a8978f52/env/train/train_resnet.py#L245C1-L257C6
#     x = torch.randn(1, 3, INPUT_DIM, INPUT_DIM, requires_grad=True).to(device)
# outputfile = f"./env/train/trail_dnn_{dnn_name}.onnx"
# torch.onnx.export(model,               # model being run
#                 x,                         # model input (or a tuple for multiple inputs)
#                 outputfile,   # where to save the model (can be a file or file-like object)
#                 export_params=True,        # store the trained parameter weights inside the model file
#                 opset_version=12,          # the ONNX version to export the model to
#                 # do_constant_folding=True,  # whether to execute constant folding for optimization
#                 do_constant_folding=False,  # whether to execute constant folding for optimization
#                 input_names = ['input'],   # the model's input names
#                 output_names = ['output'], # the model's output name
# )

<class 'densenet.DenseNet2D'>


In [5]:
# ONNX 
# onnx documentation: https://pytorch.org/tutorials/advanced/super_resolution_with_onnxruntime.html
import onnx
import onnxruntime as ort

ort_sess = ort.InferenceSession(model_outputfile) # providers = 'CUDAExecutionProvider'
onnx_model = onnx.load(model_outputfile)

# x = torch.randn(bs, 1, INPUT_XDIM, INPUT_YDIM, requires_grad=False).to(device)
# input = np.random.random((bs, 1, INPUT_XDIM, INPUT_YDIM)).astype(np.float32)
# outputs = ort_sess.run(None, {'input': input})

In [6]:
os.makedirs('test/labels/',exist_ok=True)
os.makedirs('test/mask/',exist_ok=True)
# step1: preprocess image
# IrisDataset is preprocessing for test inputs
test_set = IrisDataset(filepath = 'Semantic_Segmentation_Dataset/',\
                            split = 'test',transform = transform)
print("load")
# create iterable from preprocessed test inputs  
testloader = DataLoader(test_set, batch_size = bs,
                        shuffle=False, num_workers=2)
print("hi")
# step2
for i, batchdata in tqdm(enumerate(testloader),total=len(testloader)):
    # batchdata based on get function of IrisDataset
    img,labels,index,x,y= batchdata
    # ========== model inference ===========
    # data = img.to(device)       
    # output = model(data)
    # in1 = np.random.random((bs, 1, INPUT_XDIM, INPUT_YDIM)).astype(np.float32)
    # print("img", type(img))
    input = img.numpy() # tensor / img object -> npy
    # print(in1.shape, img.size())
    outputs = ort_sess.run(None, {'input': input})
    # parse model output 
    o = outputs[0]
    print(o.shape, type(o))
    o_tensor = torch.from_numpy(o)
    np.save('test/out/{}.npy'.format(1),o_tensor.cpu().numpy())    # todo
    predict = get_predictions(o_tensor)
    print("===========hi", len(index))
    print("******", len(predict))
    # ======================================
    for j in range (len(index)): 
        print("predict", len(predict[j]), len(predict[j][0]))
        np.save('test/labels/{}.npy'.format(index[j]),predict[j].cpu().numpy())      
        pred_img = predict[j].cpu().numpy()/3.0
        inp = img[j].squeeze() * 0.5 + 0.5
        img_orig = np.clip(inp,0,1)
        img_orig = np.array(img_orig)
        combine = np.hstack([img_orig,pred_img])
        plt.imsave('test/mask/{}.jpg'.format(index[j]),combine)

woo ! !!!!!!
load
hi


  0%|          | 0/1 [00:00<?, ?it/s]

here3 <class 'torch.Tensor'>
(1, 4, 400, 640) <class 'numpy.ndarray'>
=================== [[[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

100%|██████████| 1/1 [00:00<00:00,  1.77it/s]


In [7]:
import shutil
try:
    os.rename('test', save)
except OSError:
    shutil.rmtree(save)
    os.rename('test', save)

In [1]:
import pandas as pd
import numpy as np
data = np.load("./test10/labels/000001.npy")
df = pd.DataFrame(data)  # df = pd.DataFrame(file_dict.item()) in your case


In [6]:
df1 = df.values.reshape(-1,).tolist()
print(len(df1))


256000


In [8]:
# Find the center of concentration for the value 3
def get_center(arr):
    total_3s = 0
    sum_row = 0
    sum_col = 0

    for i in range(len(arr)):
        if df1[i] == 3:
            # Convert the flattened index to row and column indices
            row = i // 640  # Assuming 640 columns
            col = i % 640

            # Accumulate row and column indices
            sum_row += row
            sum_col += col
            total_3s += 1

    # Calculate the average row and column indices
    avg_row = sum_row / total_3s if total_3s > 0 else 0
    avg_col = sum_col / total_3s if total_3s > 0 else 0

    # Output the center of concentration
    print(f"Center of concentration for value 3: ({avg_row}, {avg_col})")
get_center(df1)

Center of concentration for value 3: (161.48498583569406, 270.0084985835694)


In [9]:
from scipy import ndimage
ndimage.measurements.center_of_mass(data) 

ModuleNotFoundError: No module named 'scipy'

In [13]:
print(data[158])

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2
 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2
 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3
 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3
 3 3 3 3 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2
 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 

In [11]:
print(len(data), len(data[0]))

400 640
